# Exam exercise: Logistic regression analysis of Berkely admission data

First load the packages:

In [ ]:
import pandas as pd
import numpy as np
import statsmodels.api as sm
import statsmodels.formula.api as smf

The following table shows the total number of admitted and rejected
applicants to the six largest departments at University of Berkeley in 1973.

|       | Admitted| Rejected|
|:------|--------:|--------:|
|Male   |     1198|     1493|
|Female |      557|     1278|

Use a $\chi^2$-test to check whether the admission statistics for
Berkeley show any sign of gender discrimination. To enter the table
in Python you can do:

In [ ]:
admit = pd.DataFrame(
    [[1198, 1493],
     [ 557, 1278]],
    index=["Male", "Female"],
    columns=["Admitted", "Rejected"]
)

Your analysis should as a minimum contain **arguments** that support: 

- Statement of hypotheses
- Calculation of expected frequencies
- Calculation of test statistic
- Calculation and interpretation of p-value.

A more detailed data set with the admissions for each department is 
available on the course web page. The variables are:

- `Gender` (male/female)
- `Dept` (department A, B, C, D, E, F)
- `Admit` (frequency of admitted for each combination)
- `Reject` (frequency of rejected for each combination)

Load the data into Python:

In [ ]:
admission = pd.read_csv("http://asta.math.aau.dk/dan/static/datasets?file=admission.dat",sep='\s+',header=0)
admission

In order to do logistic regression for this kind of data, the response is the columns `Admit` and `Reject` (which means that we model the probability of admit) :

In [ ]:
# create proportion response and total counts
admission['Total'] = admission['Admit'] + admission['Reject']
admission['Prop'] = admission['Admit'] / admission['Total']

# fit model
m0 = smf.glm('Prop ~ Gender + Dept',
             data=admission,
             family=sm.families.Binomial(),
             freq_weights=admission['Total'])

The glm-object `m0` is a logistic model with main effects of `Gender`
and `Department`.

- Investigate whether there is any effect of these predictors.

In [ ]:
print(m0.fit().summary())

Looking at the summary of `m0`:

- Is there a significant gender difference?
- What is the interpretation of the numbers in the `Dept[T.B]`-row?

We add the standardized residuals to `admission`:

In [ ]:
n = admission['Total'].to_numpy()
y = admission['Admit'].to_numpy()
mu = m0.fit().fittedvalues * n
h = m0.fit().get_influence().hat_matrix_diag
rstandard = (y - mu) / np.sqrt(n * m0.fit().fittedvalues * (1 - m0.fit().fittedvalues)) / np.sqrt(1 - h)
admission['stdRes'] = rstandard
print(admission)

- Looking at the standardized residuals, which department deviates
  heavily from the model?
- What gender is discrimated in this department?
  
Next you should fit the model with the interaction `Gender*Dept`.

- Explain what interaction means in the current context.
- Is there a significant interaction?
- In the light of your analysis, explain the reason for your
  answer to the previous question.